In [1]:
import pandas as pd
import numpy as np 
import glob
import os 

In [2]:
calendario = pd.read_csv(r"C:\Users\joao.herculano\Documents\ciclo_calendario_expandido.csv",sep=';')

calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)

calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]

calendario = calendario[calendario['MARCA'] == "QDB"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2)       #<<< MUDAR O "+2" (CICLO ATUAL + 4 PARA ACHAR O CICLO DA SUGESTÃO) EX: C202505 -> C202509
ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]

# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] ==  ciclo_mais2][:1] #"C202514"

inicio_ciclo = pd.to_datetime(filtered_calendario['INICIO CICLO'].iloc[0], format='%d/%m/%Y')
filtered_calendario['dias_ate_inicio'] = (inicio_ciclo - today).days

filtered_calendario['match'] = 1

filtered_calendario = filtered_calendario.drop(columns='id')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_14608\3809688609.py:3: UserWarning: Parsing dates in %d/%m/%Y format when dayfirst=False (the default) was specified. Pass `dayfirst=True` or specify a format to silence this warning.
  calendario['Date'] = pd.to_datetime(calendario['Date'])


In [3]:
filtered_calendario

Ciclo INICIO CICLO   FIM CICLO  DURAÇÃO MARCA       Date  NUM_CICLO  \
4706  C202514   01/12/2025  25/12/2025       25   QDB 2025-12-01         14   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  match  
4706     C2025    C202516               45      1

In [4]:
df_similares = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\QDB_EAM\QDB - C14\arquivos para geração da sugestão\SIMILARES\PRODUTOS SIMILARES - QDB.xlsx")

df_similares = pd.merge(left=df_similares,right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], how= 'left', left_on = 'CICLO SIMILAR',right_on = 'Ciclo' )

df_similares = df_similares.drop(columns=['Ciclo'])

df_similares = df_similares.rename(columns={'INICIO CICLO':'INICIO CICLO SIMILAR','FIM CICLO':'FIM CICLO SIMILAR','DURAÇÃO':'DURAÇÃO CICLO SIMILAR'})
df_similares.drop_duplicates(inplace=True)

df_similares['MATCH'] = 1

df_similares = df_similares.drop(columns=['INICIO DO CICLO',
       'FIM DO CICLO', 'DURAÇÃO CICLO','INICIO CICLO SIMILAR','FIM CICLO SIMILAR','DURAÇÃO CICLO SIMILAR'])

In [5]:
df_similares.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH'],
      dtype='object')

In [6]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\QDB_EAM\QDB - C14\arquivos para geração da sugestão\TABELA DE PEDIDO\Pedidos Semanais Especiais - QDB - 202514.xlsx")

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm') | (df_tabela['Canal'] != 'Ecomm | VD') | (df_tabela['Canal'] != 'Ecomm | Loja')] 

df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

#df_tabela = df_tabela[df_tabela['Tipo de promoção'].str.contains('Lançamentos', na=False)]

In [7]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO','MARCA'])

df_pdv = df_pdv[df_pdv['CANAL'].isin(['HIB','VD', 'CD'])]

#df_pdv = df_pdv[df_pdv['PDV'].isin([910291,910173])]

df_pdv = df_pdv[df_pdv['STATUS'] == 'ATIVO']

df_pdv['PDV DESC'] = df_pdv['DESCRIÇÃO PDV']

df_pdv['MATCH'] = 1

In [8]:
df_pdv

PDV CANAL                 DESCRIÇÃO PDV                      PDV DESC  \
26  20968   HIB              HIB ITABAIANINHA              HIB ITABAIANINHA   
27  20969   HIB             HIB MARECHAL DEOD             HIB MARECHAL DEOD   
28  20970    VD              ER SAO SEBASTIAO              ER SAO SEBASTIAO   
29  20986   HIB                  HIB OLINDINA                  HIB OLINDINA   
30  20988   HIB                 HIB QUEIMADAS                 HIB QUEIMADAS   
31  20989   HIB                HIB ENTRE RIOS                HIB ENTRE RIOS   
32  20991   HIB              HIB CAMPO ALEGRE              HIB CAMPO ALEGRE   
33  20992    VD                 ER CONC COITE                 ER CONC COITE   
34  20993    VD                   ER CANDEIAS                   ER CANDEIAS   
35  20994    VD               ER SIMOES FILHO               ER SIMOES FILHO   
36  20995    VD                    ER LAGARTO                    ER LAGARTO   
37  20996    VD                    ER ANTARES                    ER ANTARES   
38  20997    VD                ER PITANGUINHA                ER PITANGUINHA   
39  20998    CD                   CD SERRARIA                   CD SERRARIA   
40  20999   HIB                 HIB ESPLANADA                 HIB ESPLANADA   
41  21000   HIB                  HIB SANTALUZ                  HIB SANTALUZ   
42  21001   HIB                  HIB RIO REAL                  HIB RIO REAL   
46  21278    VD                    VD SOCORRO                    VD SOCORRO   
48  21375   HIB                      IPIRA HB                      IPIRA HB   
51  21383    VD               CAPIM GROSSO ER               CAPIM GROSSO ER   
52  21495   HIB              VD BARRA DOS COQ              VD BARRA DOS COQ   
56  22541    VD                  ER RIO LARGO                  ER RIO LARGO   
62  23704    VD                   ER CONDEUBA                   ER CONDEUBA   
66  23708   HIB            HIB BARRA DO CHOCA            HIB BARRA DO CHOCA   
69  23711    VD       ER VITORIA DA CONQUISTA       ER VITORIA DA CONQUISTA   
70  23712   HIB             HIB CANDIDO SALES             HIB CANDIDO SALES   
77  24255    VD                      VD Irecê                      VD Irecê   
79  24257   HIB                 Miguel Calmon                 Miguel Calmon   
81  24269    VD          COMERCIO-ER JACOBINA          COMERCIO-ER JACOBINA   
82  24293   HIB  COMERCIO-HIB MORRO DO CHAPEU  COMERCIO-HIB MORRO DO CHAPEU   
85  23813   HIB                       VALENTE                       VALENTE   

     UF   ANALISTA          SUPERVISOR STATUS ANALISTA EUD  MATCH  
26   SE   MARCYARA     Taciana Andrade  ATIVO       DIELLY      1  
27   AL   THAYLLAN  Efigênia Herculano  ATIVO         HARY      1  
28   BA   MARCYARA            FERNANDA  ATIVO       DIELLY      1  
29   BA      LUCAS             CLÁUDIA  ATIVO         HARY      1  
30   BA       LUAN             CLÁUDIA  ATIVO         HARY      1  
31   BA   MARCYARA             CLÁUDIA  ATIVO       DIELLY      1  
32   AL   THAYLLAN  Efigênia Herculano  ATIVO         HARY      1  
33   BA  JEFFERSON             CLÁUDIA  ATIVO         HARY      1  
34   BA   MARCYARA            FERNANDA  ATIVO       DIELLY      1  
35   BA      LUCAS            FERNANDA  ATIVO         HARY      1  
36   SE   MARCYARA     Taciana Andrade  ATIVO       DIELLY      1  
37   AL  JEFFERSON        Anna Schelly  ATIVO       DIELLY      1  
38   AL      LUCAS        Anna Schelly  ATIVO       DIELLY      1  
39   AL         VA        Anna Schelly  ATIVO           VA      1  
40   BA   MARCYARA             CLÁUDIA  ATIVO       DIELLY      1  
41   BA      LUCAS             CLÁUDIA  ATIVO       DIELLY      1  
42   BA      LUCAS             CLÁUDIA  ATIVO         HARY      1  
46   SE  JEFFERSON          Carla Melo  ATIVO         HARY      1  
48   BA      LUCAS            FERNANDA  ATIVO         HARY      1  
51   BA       LUAN            FERNANDA  ATIVO       DIELLY      1  
52   SE  JEFFERSON          Carla Melo  ATIVO    

In [9]:
df_pdv.columns

Index(['PDV', 'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA',
       'SUPERVISOR', 'STATUS', 'ANALISTA EUD', 'MATCH'],
      dtype='object')

In [10]:
df_similares = pd.merge(left=df_similares,right=df_pdv,right_on=['MATCH'],left_on=['MATCH'],how='inner')

df_similares = df_similares.drop_duplicates()

In [11]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\QDB_EAM\QDB - C13\arquivos para geração da sugestão\DRAFT"  # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)

df_draft['match'] = 1 

df_draft.shape


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_14608\1168637187.py:10: DtypeWarning: Columns (6) have mixed types. Specify dtype option on import or set low_memory=False.
  df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


(83561, 47)

In [12]:
df_draft = df_draft.drop(columns=['Categoria'])

In [13]:
df_draft.columns[7:25]

Index(['Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511',
       'Histórico de Vendas do Ciclo 202512',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [14]:
# Define as colunas mensais
colunas_mensais = df_draft.columns[7:25]

# Agrupa por PDV e calcula crescimento médio por PDV
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()             # soma por mês
    variacao_mensal = soma_mensal.pct_change().dropna()    # variação percentual mês a mês
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)

# Merge do resultado de volta no dataframe original
df_draft = df_draft.merge(crescimento_por_pdv, on='PDV', how='left')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_14608\1463083786.py:24: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)


In [15]:
df_similares['PDV'] = df_similares['PDV'].astype('Int64')

df_final = pd.merge(left=df_similares,right=df_draft,right_on=['PDV', 'SKU'],left_on=['PDV','PRODUTO SIMILAR'],how='left')

In [68]:
df_final.head()

SUPERVISOR CANAL  UF    PDV           PDV DESC  PRODUTO LANÇAMENTO  \
0     Taciana Andrade   HIB  SE  20968   HIB ITABAIANINHA               85925   
1  Efigênia Herculano   HIB  AL  20969  HIB MARECHAL DEOD               85925   
2            FERNANDA    VD  BA  20970   ER SAO SEBASTIAO               85925   
3             CLÁUDIA   HIB  BA  20986       HIB OLINDINA               85925   
4             CLÁUDIA   HIB  BA  20988      HIB QUEIMADAS               85925   

                 DESCRIÇÃO DO LANÇAMENTO            MARCA  CATEGORIA  \
0  PALETA MULTIFUNCIONAL DOSE DE COR 12g  QDB DOSE DE COR  MAQUIAGEM   
1  PALETA MULTIFUNCIONAL DOSE DE COR 12g  QDB DOSE DE COR  MAQUIAGEM   
2  PALETA MULTIFUNCIONAL DOSE DE COR 12g  QDB DOSE DE COR  MAQUIAGEM   
3  PALETA MULTIFUNCIONAL DOSE DE COR 12g  QDB DOSE DE COR  MAQUIAGEM   
4  PALETA MULTIFUNCIONAL DOSE DE COR 12g  QDB DOSE DE COR  MAQUIAGEM   

   MECANICA CONSUMIDOR  ...  C-2  C-1  VENDAS CICLO ATUAL  \
0                  NaN  ...  0.0  0.0                 0.0   
1                  NaN  ...  0.0  0.0                 0.0   
2                  NaN  ...  0.0  0.0                 0.0   
3                  NaN  ...  0.0  0.0                 0.0   
4                  NaN  ...  0.0  0.0                 0.0   

  PICO VENDAS SIMILAR ULTIMOS 6 CICLOS PV GINSENG PROJEÇÃO PRÓXIMO CICLO  \
0                                  0.0        1.0                    NaN   
1                                  0.0        1.0                    NaN   
2                                  0.0        2.0                    NaN   
3                                  0.0        1.0                    NaN   
4                                  0.0        1.0                    NaN   

   PROJEÇÃO PRÓXIMO CICLO + 1 SUGESTÃO METASELLIN SUGESTÃO ABASTECIMENTO  \
0                         NaN                                              
1                         NaN                                              
2                         NaN                                              
3                         NaN                                              
4                         NaN                                              

   SUGESTÃO COMERCIAL  
0                      
1                      
2                      
3                      
4                      

[5 rows x 32 columns]

In [16]:
import pyodbc
import configparser


config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\Documents\Enviador de email\credenciais.ini")

conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query = '''
SELECT 
    b.[DATA] AS Dia,
    b.pdv AS PDV,
    b.sku as 'Código do Produto',
    b.VENDAS AS Quantidade
FROM base_vendas_bi b
LEFT JOIN (
    SELECT SKU, MAX(ORIGEM) AS ORIGEM
    FROM estoque_mar
    GROUP BY SKU
) e ON b.SKU = e.SKU
'''
dfi = pd.read_sql(query, conn)
conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_14608\330515216.py:29: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfi = pd.read_sql(query, conn)


In [17]:
dfi.head()

Dia    PDV  Código do Produto Quantidade
0  2025-09-09  20998              83061          1
1  2025-09-11  20998              83061          0
2  2025-09-06  20998              83061          1
3  2025-09-25  20998              83061          1
4  2025-09-20  20998              83061          0

In [18]:
df_venda_diaria = dfi 

In [19]:
df_venda_diaria['Dia'] = pd.to_datetime(df_venda_diaria['Dia'], errors='coerce').dt.strftime('%d/%m/%Y')

In [20]:
#df_venda_diaria = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\venda diaria\FormFiltroConsultaVendaSintetica_10_07_2025_15_27_42.xls")

df_venda_diaria.head()

Dia    PDV  Código do Produto Quantidade
0  09/09/2025  20998              83061          1
1  11/09/2025  20998              83061          0
2  06/09/2025  20998              83061          1
3  25/09/2025  20998              83061          1
4  20/09/2025  20998              83061          0

In [21]:
df_venda_diaria.head()

Dia    PDV  Código do Produto Quantidade
0  09/09/2025  20998              83061          1
1  11/09/2025  20998              83061          0
2  06/09/2025  20998              83061          1
3  25/09/2025  20998              83061          1
4  20/09/2025  20998              83061          0

In [22]:
df_venda_diaria.dtypes

Dia                  object
PDV                  object
Código do Produto     int64
Quantidade           object
dtype: object

In [23]:
df_venda_diaria['Quantidade'] = df_venda_diaria['Quantidade'].astype('float')

In [24]:
df_venda_diaria.columns

Index(['Dia', 'PDV', 'Código do Produto', 'Quantidade'], dtype='object')

In [25]:
#df_venda_diaria['PDV'] = df_venda_diaria['Unidade de Negócio'].str.split("-").str[0].str.strip()

df_venda_diaria['Dia'] = pd.to_datetime(df_venda_diaria['Dia'], format='%d/%m/%Y')

df_venda_diaria = pd.merge(left=df_venda_diaria,right=calendario[['Ciclo','Date']],left_on='Dia',right_on='Date',how='inner')

df_venda_diaria = df_venda_diaria.drop(columns='Date')

df_venda_diaria.shape

(8307689, 5)

In [26]:
# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
df_venda_diaria = df_venda_diaria.sort_values(by=['PDV', 'Código do Produto', 'Dia'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_venda_diaria['Quantidade Acumulada'] = (
    df_venda_diaria
    .groupby(['PDV', 'Código do Produto'])['Quantidade']
    .cumsum()
)  # acumulado por grupo até a data da linha

df_venda_diaria.shape

(8307689, 6)

In [27]:
df_venda_diaria = df_venda_diaria.drop_duplicates()

df_venda_agrupado = df_venda_diaria.groupby(['PDV', 'Código do Produto','Ciclo'])['Quantidade Acumulada'].max().reset_index()
df_venda_agrupado

PDV  Código do Produto    Ciclo  Quantidade Acumulada
0        11111              48130  C202308                   0.0
1        11201              58729  C202506                   0.0
2        11201              87408  C202504                   0.0
3        11201              87408  C202505                   0.0
4        11201              87408  C202506                   0.0
...        ...                ...      ...                   ...
2516687  72110              87373  C202413                  16.0
2516688   8074              43151  C202504                   0.0
2516689   8074              43151  C202505                   0.0
2516690   8074              48676  C202510                   0.0
2516691   8074              82689  C202510                   0.0

[2516692 rows x 4 columns]

In [28]:
df_venda_agrupado['Quantidade Acumulada'].sum()

np.float64(229042652.701)

In [29]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], right_on='match',left_on='MATCH',how='left')
df_final.shape

(124, 76)

In [30]:
#df_final = df_final.drop(columns=['PDV DESC','status','SKU','Descrição','Lançamento','Item analisado','Planograma','Quantidade por caixa'])

In [31]:
df_final = pd.merge(left=df_final, right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], right_on='Ciclo',left_on='CICLO SIMILAR',how='left')
df_final.shape

df_final = df_final.drop_duplicates()

In [32]:

df_venda_agrupado = df_venda_agrupado.rename(columns={'Quantidade Acumulada':'Vendas Ciclo Lançamento'})

In [33]:
df_final['PRODUTO LANÇAMENTO'] = df_final['PRODUTO LANÇAMENTO'].astype('Int64')

df_venda_agrupado['PDV'] = df_venda_agrupado['PDV'].astype('Int64')

df_final = pd.merge(left=df_final, right = df_venda_agrupado, right_on=['Ciclo','Código do Produto','PDV'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final = df_final.drop_duplicates()

In [34]:
df_final['PDV'].value_counts().min()

np.int64(4)

In [35]:
df_final.columns[31:48]

Index(['Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511',
       'Histórico de Vendas do Ciclo 202512',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [36]:
colunas = df_final.columns[31:48]

df_final[colunas] = df_final[colunas].fillna(0)


In [37]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[31:48]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO_GERAL'] = 0.2

CRESCIMENTO


np.float64(0.2027)

In [38]:
df_final = df_final.drop(columns='Ciclo_y')

df_final = df_final.rename(columns={'Ciclo_x': 'Ciclo',	'INICIO CICLO_x': 'INICIO CICLO',	'FIM CICLO_x':'FIM CICLO' ,'DURAÇÃO_x':'DURAÇÃO',
                                    	'INICIO CICLO_y': 'INICIO CICLO SIMILAR' ,	'FIM CICLO_y': 'FIM CICLO SIMILAR','DURAÇÃO_y':'DURAÇÃO CICLO SIMILAR'})

In [39]:
df_final.columns[41:48]

Index(['Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511',
       'Histórico de Vendas do Ciclo 202512',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [40]:
VENDA_SIMILAR_6_MESES= df_final.columns[41:48]

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)


df_final['MEDIANA DO HISTÓRICO'] = df_final[colunas_mensais].dropna().median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[colunas_mensais].dropna().mean(axis=1)

df_final['Vendas Ciclo Lançamento'] = df_final['Vendas Ciclo Lançamento'].fillna(0)

In [41]:
df_final['MEDIANA DO HISTÓRICO USADA'] = np.where(df_final['MEDIA DO HISTÓRICO']<df_final['MEDIANA DO HISTÓRICO'],df_final['MEDIANA DO HISTÓRICO'],df_final['MEDIA DO HISTÓRICO'])



In [42]:
df_depara_vdc = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\Vitoria da Conquista\HISTORICO VENDAS VITORIA DA CONQUISTA\Filiais - Vitoria da Conquista 4.xlsx")


df_vdc = pd.read_parquet(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\Vitoria da Conquista\HISTORICO VENDAS VITORIA DA CONQUISTA\vendas_compilado_VDC.parquet")


########################################
df_vdc['Quantidade Acumulada vdc'] = (
        df_vdc
        .groupby(['Practico', 'Código'])['Quantidade']
        .cumsum())


In [43]:
df_vdc=df_vdc.rename(columns={'Practico':'PDVDEPARA.Practico'})
df_vdc.head()

Ciclo PDVDEPARA.Practico  Código                            Descrição  \
0  C202201              23701    1061       SOPHIE LOC HID CPO MOANA 200ml   
1  C202201              23701    1078      MATCH SRUM CAP POS QUIMICA 50ml   
2  C202201              23701    1296  PMPCK THE BLEND DES ANTIT AER 2x75g   
3  C202201              23701    1302       PMPCK LILY DES ANTIT AER 2x75g   
4  C202201              23701    1314       PMPCK ZAAD DES ANTIT AER 2x75g   

   Quantidade  Quantidade Acumulada vdc  
0           5                         5  
1           1                         1  
2           1                         1  
3           6                         6  
4           7                         7

In [44]:
df_vdc_agrupado = df_vdc.groupby(['PDVDEPARA.Practico',	'Código','Ciclo'])['Quantidade Acumulada vdc'].max().reset_index()

df_vdc_agrupado = df_vdc_agrupado.rename(columns={'Ciclo':'Ciclo vdc'})

df_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].fillna(0)

df_vdc_agrupado.head()

PDVDEPARA.Practico  Código Ciclo vdc  Quantidade Acumulada vdc
0              23701    1004   C202203                        37
1              23701    1004   C202204                        59
2              23701    1004   C202205                        63
3              23701    1004   C202206                        69
4              23701    1004   C202207                        75

In [45]:
df_vdc_agrupado = df_vdc_agrupado[df_vdc_agrupado['PDVDEPARA.Practico'] != 'nan']

In [46]:
df_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].astype('Int64')

In [47]:
df_final = pd.merge(left=df_final, right = df_vdc_agrupado, right_on=['Ciclo vdc','Código','PDVDEPARA.Practico'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final['Quantidade Acumulada vdc'] = df_final['Quantidade Acumulada vdc'].fillna(0)


df_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada vdc']>0, df_final['Quantidade Acumulada vdc'], df_final['Vendas Ciclo Lançamento'])

df_final = df_final.drop(columns='Quantidade Acumulada vdc')


df_final = df_final.drop(columns='Ciclo vdc')



In [48]:
medi = df_final.groupby(['CANAL','UF'])['MEDIANA DO HISTÓRICO USADA'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO USADA':'med_por_canal'})
medi

CANAL   UF  med_por_canal
0     CD   AL       1.529412
1    HIB   AL       0.294118
2    HIB   BA       0.823529
3    HIB  BA3       0.000000
4    HIB   SE       0.058824
5    HIB  VDC       0.058824
6     VD   AL       1.411765
7     VD   BA       1.235294
8     VD  BA3       0.235294
9     VD   SE       0.764706
10    VD  VDC       1.000000

In [49]:
df_final = pd.merge(left=df_final, right=medi,on=['CANAL','UF'],how='inner')




In [50]:
df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_GERAL'] + CRESCIMENTO #crescimento do pdv

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + CRESCIMENTO>0.8,0.8,df_final['CRESCIMENTO_GERAL'] + CRESCIMENTO)

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']<0,0,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

#df_final['MEDIANA DO HISTÓRICO USADA'] = np.where(df_final['MEDIANA DO HISTÓRICO']==0, df_final['med_por_canal'],df_final['MEDIANA DO HISTÓRICO'])


In [51]:
df_final['med_por_canal'].isna().sum()

np.int64(0)

In [52]:

# Primeiro cálculo intermediário
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO_FINAL'] * df_final['Vendas Ciclo Lançamento'] + df_final['Vendas Ciclo Lançamento'] < df_final['MEDIANA DO HISTÓRICO USADA'],
                                    round(df_final['CRESCIMENTO_FINAL'] * df_final['MEDIANA DO HISTÓRICO USADA']+ df_final['MEDIANA DO HISTÓRICO USADA'],0), 
                                    round(df_final['CRESCIMENTO_FINAL']*df_final['Vendas Ciclo Lançamento']+df_final['Vendas Ciclo Lançamento'],0))

df_final['PV GINSENG'] = np.where(df_final['PV GINSENG'].isna(),df_final['med_por_canal'] ,df_final['PV GINSENG'])

df_final.shape

(124, 92)

In [53]:
df_final.columns[29:42]

Index(['Desativação', 'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507'],
      dtype='object')

In [54]:
df_final.drop(columns=df_final.columns[29:42],inplace=True)

In [55]:
df_final.columns[29:35]

Index(['Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511',
       'Histórico de Vendas do Ciclo 202512',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [56]:
df_final = df_final.rename(columns={df_final.columns[30]: "C-4", df_final.columns[31]: "C-3",df_final.columns[32]: "C-2",df_final.columns[33]: "C-1",df_final.columns[34]:'VENDAS CICLO ATUAL'})


In [57]:
df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR', 'STATUS',
       'ANALISTA EUD', 'Classe', 'SKU', 'Descrição', 'Subcategoria',
       'Lançamento', 'Histórico de Vendas do Ciclo 202508', 'C-4', 'C-3',
       'C-2', 'C-1', 'VENDAS CICLO ATUAL', 'Dias sem venda',
       'Projeção Próximo Ciclo', 'Projeção Próximo Ciclo + 1',
       'Promoção Próximo Ciclo', 'Promoção Próximo Ciclo + 1', 'Estoque Atual',
       'Estoque em Transito', 'Pedido Pendente',
       'Compra inteligente semanal/Sugestão de compra',
       'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1', 'Item Desativado',
       'Data Prevista Regularização', 'Carteira Bloqueada Para Novos

In [58]:

df_final.drop(columns=['match_x','match_y','STATUS', 'Classe','Promoção Próximo Ciclo', 'Promoção Próximo Ciclo + 1',
                        'Compra inteligente semanal/Sugestão de compra',
       'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1', 'Item Desativado',
       'Data Prevista Regularização', 'Carteira Bloqueada Para Novos Pedidos',
       'Planograma', 'Quantidade por caixa','Quantidade',
       'Item analisado', 'match_x', 'CRESCIMENTO', 'Ciclo', 'INICIO CICLO',
       'FIM CICLO', 'DURAÇÃO', 'match_y', 'dias_ate_inicio',
       'INICIO CICLO SIMILAR', 'FIM CICLO SIMILAR', 'DURAÇÃO CICLO SIMILAR','Ciclo',
       'CRESCIMENTO_GERAL','PDVDEPARA.Practico', 'Código',
       'med_por_canal', 'CRESCIMENTO_FINAL'],inplace=True)
df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR',
       'ANALISTA EUD', 'SKU', 'Descrição', 'Subcategoria', 'Lançamento',
       'Histórico de Vendas do Ciclo 202508', 'C-4', 'C-3', 'C-2', 'C-1',
       'VENDAS CICLO ATUAL', 'Dias sem venda', 'Projeção Próximo Ciclo',
       'Projeção Próximo Ciclo + 1', 'Estoque Atual', 'Estoque em Transito',
       'Pedido Pendente', 'Preço Sell In',
       'Histórico de Vendas do Ciclo 202513', 'Código do Produto',
       'Vendas Ciclo Lançamento', 'Pico Vendas Similar Ultimos 6 ciclos',
       'MEDIANA DO HISTÓRICO', 'MEDIA DO HISTÓRICO',
       'MEDIANA DO HISTÓRICO USADA', 'PV GINSENG'],
      dtype='object')

In [59]:
df_final.columns = df_final.columns.str.upper()

df_final.drop(columns=df_final.filter(regex='HISTÓRICO DE VENDAS DO CICLO').columns, inplace=True)

df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR',
       'ANALISTA EUD', 'SKU', 'DESCRIÇÃO', 'SUBCATEGORIA', 'LANÇAMENTO', 'C-4',
       'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL', 'DIAS SEM VENDA',
       'PROJEÇÃO PRÓXIMO CICLO', 'PROJEÇÃO PRÓXIMO CICLO + 1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'PREÇO SELL IN',
       'CÓDIGO DO PRODUTO', 'VENDAS CICLO LANÇAMENTO',
       'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS', 'MEDIANA DO HISTÓRICO',
       'MEDIA DO HISTÓRICO', 'MEDIANA DO HISTÓRICO USADA', 'PV GINSENG'],
      dtype='object')

In [60]:
df_final = df_final.drop(columns=['DESCRIÇÃO','MEDIANA DO HISTÓRICO'])

In [61]:
df_final.shape

(124, 44)

In [62]:
df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR',
       'ANALISTA EUD', 'SKU', 'SUBCATEGORIA', 'LANÇAMENTO', 'C-4', 'C-3',
       'C-2', 'C-1', 'VENDAS CICLO ATUAL', 'DIAS SEM VENDA',
       'PROJEÇÃO PRÓXIMO CICLO', 'PROJEÇÃO PRÓXIMO CICLO + 1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'PREÇO SELL IN',
       'CÓDIGO DO PRODUTO', 'VENDAS CICLO LANÇAMENTO',
       'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS', 'MEDIA DO HISTÓRICO',
       'MEDIANA DO HISTÓRICO USADA', 'PV GINSENG'],
      dtype='object')

In [63]:
df_final = df_final.reindex(columns=[
    'SUPERVISOR',
    'CANAL',
    'UF',
    'PDV',
    'PDV DESC',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    'MECANICA CONSUMIDOR',
    '% CONSUMIDOR',
    'MECANICA REVENDEDOR',
    '% REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG',
    'PROJEÇÃO PRÓXIMO CICLO',
    'PROJEÇÃO PRÓXIMO CICLO + 1',
    ])


In [64]:
df_final['SUGESTÃO METASELLIN'] = ''
df_final['SUGESTÃO ABASTECIMENTO'] = ''
df_final['SUGESTÃO COMERCIAL'] = ''


In [65]:
df_final['PV GINSENG'] = np.ceil(df_final['PV GINSENG'])

In [66]:
df_final.to_excel(r'C:\Users\joao.herculano\Documents\lançamentoQDB14-10.xlsx',index=False)